In [1]:
import os
import re
import nltk
import pandas as pd
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer

In [3]:
import os
import re
import pandas as pd

# Initialize DataFrame
df = pd.DataFrame(columns=['Hotel', 'Review'])

# Path to the data directory
data_dir = './data'

# Regex pattern to remove date
date_pattern = re.compile(r'\b\w{3}\s+\d{1,2}\s+\d{4}\b')

# Traverse directory
for city_folder in os.listdir(data_dir):
    city_path = os.path.join(data_dir, city_folder)
    if os.path.isdir(city_path):
        for file in os.listdir(city_path):
            hotel_name = file.replace('_', ' ')
            file_path = os.path.join(city_path, file)
            with open(file_path, 'r', encoding='ISO-8859-1') as f:
                content = f.read()
                reviews = date_pattern.sub('', content).split('\n')
                for review in reviews:
                    if review.strip():
                        df = df.append({'Hotel': hotel_name, 'Review': review.strip()}, ignore_index=True)

# Save DataFrame to CSV
df.to_csv('hotel_reviews.csv', index=False)

C:\Users\durud\AppData\Local\Temp\ipykernel_14596\2444659671.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'Hotel': hotel_name, 'Review': review.strip()}, ignore_index=True)
C:\Users\durud\AppData\Local\Temp\ipykernel_14596\2444659671.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'Hotel': hotel_name, 'Review': review.strip()}, ignore_index=True)
C:\Users\durud\AppData\Local\Temp\ipykernel_14596\2444659671.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'Hotel': hotel_name, 'Review': review.strip()}, ignore_index=True)
C:\Users\durud\AppData\Local\Temp\ipykernel_14596\2444659671.py:26: FutureWarning: The frame.append method is deprecated and will be removed f

In [4]:
stop_words = set(stopwords.words('english'))
lemmatizer = WordNetLemmatizer()

In [5]:
def preprocess_text(text):
    # Normalize text
    text = text.lower()  # Convert to lowercase
    text = re.sub(r'\b\w{1,2}\b', '', text)  # Remove words with 1-2 letters
    text = re.sub(r'[^\w\s]', '', text)
    text = re.sub(r'[^a-z\s]', '', text)  # Remove non-alphabetic characters

    # Tokenize text
    tokens = word_tokenize(text)

    # Remove stopwords and lemmatize
    cleaned_tokens = [lemmatizer.lemmatize(word) for word in tokens if word not in stop_words]
    
    return ' '.join(cleaned_tokens)

In [6]:
df['Processed_Review'] = df['Review'].apply(preprocess_text)


In [8]:
display(df.head(100))
df.to_csv('hotel_reviews2.csv', index=False)

Hotel  \
0     china beijing aloft beijing haidian   
1     china beijing aloft beijing haidian   
2     china beijing aloft beijing haidian   
3     china beijing aloft beijing haidian   
4     china beijing aloft beijing haidian   
..                                    ...   
95      china beijing bamboo garden hotel   
96   china beijing beijing century towers   
97   china beijing beijing century towers   
98  china beijing beijing dong fang hotel   
99  china beijing beijing dong fang hotel   

                                               Review  \
0   Nice trendy hotel location not too bad.\tI sta...   
1   Great Budget Hotel!\tStayed two nights at Alof...   
2   Excellent value - location not a big problem.\...   
3   Stylish clean reasonable value poor location\t...   
4   Remote but excellent value for money\tStayed t...   
..                                                ...   
95                                          Un trésor   
96  Nice property\tWe booked a three bedroom room ...   
97  Great hotel for large groups! (and individuals...   
98  Disappointed\tThe hotel is out of the city cen...   
99  good value\tThe hotel is a well located good a...   

                                     Processed_Review  
0   nice trendy hotel location bad stayed hotel on...  
1   great budget hotel stayed two night aloft rece...  
2   excellent value location big problem stayed al...  
3   stylish clean reasonable value poor location g...  
4   remote excellent value money stayed one night ...  
..                                                ...  
95                                              trsor  
96  nice property booked three bedroom room nite r...  
97  great hotel large group individual traveled be...  
98  disappointed hotel city centre minute walk squ...  
99  good value hotel well located good quality sta...  

[100 rows x 3 columns]

In [7]:
from sklearn.feature_extraction.text import TfidfVectorizer

# Initialize and fit TF-IDF vectorizer
vectorizer = TfidfVectorizer(max_features=1000)
X = vectorizer.fit_transform(df['Processed_Review'])  # Assuming 'Processed_Review' contains your cleaned text data
